In [263]:
# Using plotly
import plotly.graph_objects as go
import numpy as np

Define data

In [264]:
import pandas as pd
data = pd.read_csv('stack_and_functions.csv').to_dict(orient='records')

Create block diagram

In [266]:
import plotly.graph_objects as go
import random

# If there is no end, set it to start + 0x1000
for d in data:
    if 'end' not in d:
        d['end'] = d['start'] + 0x5000

# If there is no start, set it to end - 0x1000
for d in data:
    if 'start' not in d:
        d['start'] = d['end'] - 0x5000

# Sort the data by start
data = sorted(data, key=lambda x: x['start'])
total_used_len = sum([d['end']-d['start'] for d in data]) # Length of all blocks described
tickpointers = []

def random_color():
    return f'#{random.randint(0, 0xFFFFFF):06x}'

# Create a square for each index
fig = go.Figure()
for i, d in enumerate(data):
    if i == 0:
        prev_y = 0
    max_y = (prev_y + ((d['end'] - d['start']) / total_used_len))
    fillcolor = random_color()

    if d['Order'] == "ENTRY":
        x0 = 0
    else:
        x0 = 0.1

    fig.add_shape(
        type="rect",
        x0=x0,
        y0=prev_y * len(data),
        x1=0 + 1,
        y1=max_y * len(data),
        line=dict(width=2),
        fillcolor=fillcolor,
        opacity=0.5,
        layer="below",
    )

    tickpoint = [(prev_y + (max_y - prev_y) / 2) * len(data)]
    tickpointers.extend([prev_y * len(data)])

    fig.add_trace(go.Scatter
    (
        x=[0.5],
        y=tickpoint,
        text=d['name'],
        mode="text",
        textposition="middle center",
        name=d['name'],
        # Set color to
        marker=dict(
            color=fillcolor,
        ),
    ))
    
    prev_y = max_y

fig.update_xaxes(
    range=[0, 1],
    tickvals=[0, 1],
)

labels = [hex(value) for d in data for value in (d.get('start'), d['end']) if 'end' in d]

# If label is not the first in labels or the last entry, merge the label with the next label
labelset = []
for i in range(0, len(labels), 2):
    if i == 0:
        labelset.append(labels[i])
    elif i == len(labels) - 1:
        labelset.append(labels[i])
    else:
        labelset.append(f"{labels[i+1]}<br>{labels[i]}")
labelset.append(labels)

fig.update_yaxes(
    # tickvals=[i for i in range(len(data)+1)], 
    tickvals = tickpointers,
    ticktext=labelset,
    griddash="longdashdot",
    gridwidth=0,
    gridcolor="black",
    showgrid=False,
)

fig.update_xaxes(
    # Disable ticks
    showticklabels=False,
)

fig.update_layout(
    width=1000,
    height=1200,
    autosize=True,
    margin=dict(l=200, r=20, t=20, b=20),
    font=dict(
        size=18,
    ),
    # Legend being the name of the function
    legend_title_text="Function/Locations",
)

fig.show()